In [6]:
# Dependencies
# ----------------------------------
import pandas as pd

# Imports the method used for connecting to DBs
from sqlalchemy import create_engine

# Imports the methods needed to abstract classes into tables
from sqlalchemy.ext.declarative import declarative_base

# Allow us to declare column types
from sqlalchemy import Column, Integer, String, Float 

from sqlalchemy import create_engine, Column, Integer, String
Base = declarative_base()

In [3]:
oscars_df = pd.read_csv('output/final_oscars.csv')
imdb_df = pd.read_csv('output/cleaned_imdb.csv')

C:\Users\gucas\anaconda3\envs\PythonData\lib\site-packages\IPython\core\interactiveshell.py:3072: DtypeWarning: Columns (3) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [7]:
# Create the Classes
class Directors(Base):
    __tablename__ = 'directors'
    director_id = Column(String, primary_key=True)
    director_name = Column(String(255))
    
class Movies(Base):
    __tablename__ = 'movies'
    movie_id = Column(String, primary_key=True)
    movie_title = Column(String(255))
    year = Column(Integer)
    director_id = Column(String(255), foreign_key=True)
    reviews_from_users = Column(Float)
    reviews_from_critics = Column(Float)

class Oscar_categories(Base):
    __tablename__ = 'oscar_categories'
    oscar_id = Column(String, primary_key=True)
    award_category = Column(String(255))
    
class Movie_awards(Base):
    __tablename__ = 'movie_awards'
    movie_id = Column(String, primary_key=True)
    oscar_id = Column(String(255), primary_key=True)

class Directing_awards(Base):
    __tablename__ = 'directing_awards'
    director_id = Column(String, primary_key=True)
    oscar_id = Column(String(255), primary_key=True)

C:\Users\gucas\anaconda3\envs\PythonData\lib\site-packages\sqlalchemy\sql\base.py:302: SAWarning: Can't validate argument 'foreign_key'; can't locate any SQLAlchemy dialect named 'foreign'
  % (k, dialect_name)


In [8]:
# These tables only exists in python and not in the actual database
Base.metadata.tables

immutabledict({'directors': Table('directors', MetaData(bind=None), Column('director_id', String(), table=<directors>, primary_key=True, nullable=False), Column('director_name', String(length=255), table=<directors>), schema=None), 'movies': Table('movies', MetaData(bind=None), Column('movie_id', String(), table=<movies>, primary_key=True, nullable=False), Column('movie_title', String(length=255), table=<movies>), Column('year', Integer(), table=<movies>), Column('director_id', String(length=255), table=<movies>), Column('reviews_from_users', Float(), table=<movies>), Column('reviews_from_critics', Float(), table=<movies>), schema=None), 'oscar_categories': Table('oscar_categories', MetaData(bind=None), Column('oscar_id', String(), table=<oscar_categories>, primary_key=True, nullable=False), Column('award_category', String(length=255), table=<oscar_categories>), schema=None), 'movie_awards': Table('movie_awards', MetaData(bind=None), Column('movie_id', String(), table=<movie_awards>, p

In [13]:
database = "movies_db"
username = 'postgres'
password = '868789'
host = 'localhost'
port = 5432

In [14]:
# Create our database engine
engine = create_engine(f"postgresql://{username}:{password}@{host}:{port}/{database}") 

In [15]:
# This is where we create our tables in the database
Base.metadata.create_all(engine)

In [49]:
# The ORM’s “handle” to the database is the Session.
from sqlalchemy.orm import Session
session = Session(engine)

In [38]:
# Read csv for directors
directors_df = pd.read_csv('output/directors.csv',  index_col=0)
directors_df

name
0                            Alexander Black
1                               Charles Tait
2                                  Urban Gad
3                         Charles L. Gaskill
4                        Francesco Bertolini
...                                      ...
36590                         Geethika Sudip
36591                             Steve Noir
36592                           Erik Verkerk
36593   Syed Nurfaiz Khalid bin Syed Ibrahim
36594                         Nando Martínez

[36595 rows x 1 columns]

In [39]:
# Note that adding to the session does not update the table. It queues up those queries.
# Adding data to directors table from directors csv file
count = 0
for name in directors_df['name']:
    session.add(Directors(director_id=count, director_name=name))
    count +=1

In [40]:
session.new

IdentitySet([<__main__.Directors object at 0x000001D8F4A912B0>, <__main__.Directors object at 0x000001D8F4A91518>, <__main__.Directors object at 0x000001D8F4A917B8>, <__main__.Directors object at 0x000001D8F4A913C8>, <__main__.Directors object at 0x000001D8F4A91470>, <__main__.Directors object at 0x000001D8F4A91358>, <__main__.Directors object at 0x000001D8F4A91208>, <__main__.Directors object at 0x000001D8F4A91668>, <__main__.Directors object at 0x000001D8F4A91198>, <__main__.Directors object at 0x000001D8F4A91710>, <__main__.Directors object at 0x000001D8F4A917F0>, <__main__.Directors object at 0x000001D8F4A91860>, <__main__.Directors object at 0x000001D8F4A918D0>, <__main__.Directors object at 0x000001D8F4A91940>, <__main__.Directors object at 0x000001D8F4A919B0>, <__main__.Directors object at 0x000001D8F4A91A20>, <__main__.Directors object at 0x000001D8F4A91A90>, <__main__.Directors object at 0x000001D8F4A91B00>, <__main__.Directors object at 0x000001D8F4A91B70>, <__main__.Director

In [50]:
imdb_df = pd.read_csv('output/cleaned_imdb.csv',  index_col=0)
imdb_df

imdb_title_id                  title  year                     genre  \
47984     tt0465963                   1:01  2006                     Drama   
78824     tt5834036                   1:54  2016              Drama, Sport   
52277     tt1002561                   2:13  2009  Drama, Mystery, Thriller   
56146     tt1261041                   2:22  2008    Crime, Drama, Thriller   
48285     tt0472582                   2:37  2006                     Drama   
...             ...                    ...   ...                       ...   
68459     tt2723138          Zyvie Belarus  2013          Biography, Drama   
13349     tt0062529         Zywot Mateusza  1968                     Drama   
46417     tt0429277              Zyzzyx Rd  2006    Crime, Drama, Thriller   
41142     tt0301770  Zzikhimyeon jukneunda  2000          Horror, Thriller   
1265      tt0022731                 #NAME?  1932                    Comedy   

               country                   director  \
47984      Denmark, UK          Annette K. Olesen   
78824           Canada                Yan England   
52277              USA            Charles Adelman   
56146           Canada             Phillip Guzman   
48285        Australia         Murali K. Thalluri   
...                ...                        ...   
68459  Poland, Belarus      Krzysztof Lukaszewicz   
13349           Poland         Witold Leszczynski   
46417              USA                John Penney   
41142      South Korea  Gi-hun Kim, Jong-seok Kim   
1265               USA                Jack Conway   

                                       writer         production_company  \
47984                        Kim Fupz Aakeson                Sigma Films   
78824                             Yan England         Cinémaginaire Inc.   
52277                           Mark Thompson            Anthem Pictures   
56146              Mick Rossi, Phillip Guzman           Lab4 Productions   
48285                      Murali K. Thalluri              Kojo Pictures   
...                                       ...                        ...   
68459  Krzysztof Lukaszewicz, Franak Viacorka                        NaN   
13349     Witold Leszczynski, Wojciech Solarz           P.P. Film Polski   
46417                             John Penney                 Zyzzyx LLC   
41142                           Chang-hak Han      Sam Wu Communications   
1265               Ivor Novello, Ivor Novello  Metro-Goldwyn-Mayer (MGM)   

       reviews_from_users  reviews_from_critics  
47984                 3.0                  11.0  
78824                19.0                  14.0  
52277                14.0                   3.0  
56146                19.0                   5.0  
48285                77.0                  42.0  
...                   ...                   ...  
68459                 1.0                   2.0  
13349                 2.0                   1.0  
46417                11.0                   2.0  
41142                10.0                   9.0  
1265                 19.0                   3.0  

[85855 rows x 10 columns]

In [51]:
# Adding data to movies table from imdb csv file
for index, name in imdb_df.iterrows():
    session.add(Movies(movie_id=name['imdb_title_id'], movie_title=name['title'], year=name['year'], reviews_from_users=name['reviews_from_users'], reviews_from_critics=name['reviews_from_critics']))


In [52]:
session.new

IdentitySet([<__main__.Movies object at 0x000001D8877599E8>, <__main__.Movies object at 0x000001D89312F1D0>, <__main__.Movies object at 0x000001D89312F518>, <__main__.Movies object at 0x000001D89312FBE0>, <__main__.Movies object at 0x000001D89312FCC0>, <__main__.Movies object at 0x000001D89312FD30>, <__main__.Movies object at 0x000001D89312FC88>, <__main__.Movies object at 0x000001D89312FE10>, <__main__.Movies object at 0x000001D89312F940>, <__main__.Movies object at 0x000001D89312F6D8>, <__main__.Movies object at 0x000001D89312F278>, <__main__.Movies object at 0x000001D89312F2B0>, <__main__.Movies object at 0x000001D89312F7F0>, <__main__.Movies object at 0x000001D89312FA58>, <__main__.Movies object at 0x000001D89312F550>, <__main__.Movies object at 0x000001D89312F5C0>, <__main__.Movies object at 0x000001D89312F588>, <__main__.Movies object at 0x000001D89312FE48>, <__main__.Movies object at 0x000001D89312FEB8>, <__main__.Movies object at 0x000001D89312FF28>, <__main__.Movies object at 

In [53]:
session.commit()

In [55]:
# Read csv for oscars categories
oscars_categories = pd.read_csv('output/oscars_categories.csv',  index_col=0)
oscars_categories

categories
0                         DIRECTING
1  CINEMATOGRAPHY (Black-and-White)
2            CINEMATOGRAPHY (Color)
3               BEST MOTION PICTURE
4                      BEST PICTURE

In [57]:
# Adding data to oscars categories table from csv file
count = 0
for index, name in oscars_categories.iterrows():
    session.add(Oscar_categories(oscar_id=count, award_category=name['categories']))
    count +=1

In [58]:
session.commit()

In [48]:
# Movie_awards
# movie_id
# oscar_id

In [ ]:
# Directing_awards
# director_id
# oscar_id

In [59]:
session.close()